In [32]:
import asyncio
from pathlib import Path  # Используем pathlib для удобной и кросс-платформенной работы с путями
import uuid

from typing import Optional, Coroutine, Any
import os
from sensory_data_client import DataClient, get_settings, DataClientConfig, PostgresConfig, MinioConfig, create_data_client, ElasticsearchConfig
from sensory_data_client.models.document import DocumentCreate, DocumentMetadata
from sensory_data_client.models import GroupCreate

# cfg = DataClientConfig(postgres = PostgresConfig(user = "postgres",
#                                                            password = "postgres",
#                                                            host = "10.10.0.70",
#                                                            port=5422), 
#                                             minio = MinioConfig(endpoint="10.10.0.70:9008",  bucket = "documents"))
def _build_client() -> "DataClient":
    # Подтяните конфиг как у вас принято (из env или явный)
    pg = PostgresConfig(
        host=os.getenv("POSTGRES_HOST","10.10.0.70"),
        port=int(os.getenv("POSTGRES_PORT","5422")),
        user=os.getenv("POSTGRES_USER","postgres"),
        password=os.getenv("POSTGRES_PASSWORD","postgres"),
        database=os.getenv("POSTGRES_DB","documents"),
    )
    mn = MinioConfig(
        endpoint=os.getenv("MINIO_ENDPOINT","10.10.0.70:9008"),
        bucket=os.getenv("MINIO_BUCKET","documents"),
        secure=False,
    )
    es = ElasticsearchConfig(
        endpoint=os.getenv("ELASTIC_ENDPOINT","http://10.10.0.70:9200"),
        username=os.getenv("ELASTIC_USER", "user"),
        password=os.getenv("ELASTIC_PASSWORD, user"),
        api_key=os.getenv("ELASTIC_API_KEY"),
        verify_certs=bool(int(os.getenv("ELASTIC_VERIFY","0"))),
        index_lines=os.getenv("ES_INDEX_LINES","doc_lines_v1"),
        index_docs=os.getenv("ES_INDEX_DOCS","docs_v1"),
    )
    cfg = DataClientConfig(postgres=pg, minio=mn, elastic=es)
    return create_data_client(cfg)

client = _build_client()
await client.check_connections()

endpoint='10.10.0.70:9008' accesskey='minioadmin' secretkey='minioadmin' bucket='documents' secure=False


{'postgres': 'ok', 'minio': 'ok', 'elastic': 'ok'}

In [2]:

lines  = await client.list_doclines()
objects = await client.list_stor(prefix="pdf/")

In [2]:
email = await client.get_user_by_email("fox@sensorylab.ru")
email


In [14]:
email = await client.create_user(email="fox@sensorylab.ru", plain_password="1qa2ws#ED")


In [15]:

group = await client.create_group(GroupCreate(name="Первые пташкиbu", description="Ну пацаны нормальные"))


In [100]:


file_path_str = r"X:\Telegram Desktop\ai-hr-2024.pdf"
file_path = Path(file_path_str)

# Проверка, что файл существует, перед тем как его читать
if not file_path.is_file():
    print(f"Ошибка: Файл не найден по пути {file_path}")

print(f"Подготовка к загрузке файла: {file_path}")

# Шаг 2: Читаем файл в байты
# .read_bytes() - простой способ прочитать весь файл в память
try:
    file_content: bytes = file_path.read_bytes()
except Exception as e:
    print(f"Не удалось прочитать файл: {e}")
    

# Шаг 3: Создаем объект метаданных DocumentCreate
# Извлекаем информацию из пути и добавляем остальную
document_meta = DocumentCreate(
    user_document_id=str(uuid.uuid4()), # Генерируем уникальный ID для этого документа
    name=file_path.name,                # 'X5Group x SensoryLAB 07.02.2024.pptx.pdf'
    owner_id=email.id,             # ID пользователя, который загружает файл
    access_group_id=group.id,         # Опциональная группа доступа
    metadata=DocumentMetadata()
)


Подготовка к загрузке файла: X:\Telegram Desktop\ai-hr-2024.pdf


In [101]:

# Шаг 4: Вызываем асинхронный метод с `await`
try:
    # Ваш метод `upload_file` скорее всего захочет получить чистое имя файла,
    # а не весь путь. file_path.name идеально для этого подходит.
    result_document = await client.upload_file(
        file_name=file_path.name,
        content=file_content,
        meta=document_meta
    )
    
    print("\n✅ Успешно загружен документ!")
    print(f"   ID в базе: {result_document.id}")
    print(f"   Путь в хранилище: {result_document}")

except Exception as e:
    print(f"❌ Произошла ошибка во время загрузки: {e}")



✅ Успешно загружен документ!
   ID в базе: 1101a973-12f5-4c49-b195-95666b76d3bd
   Путь в хранилище: user_document_id='37908006-7c16-45b7-a034-f360c33fef27' name='ai-hr-2024.pdf' owner_id=UUID('0d6b6faf-04a0-4358-93a0-411184b63840') access_group_id=UUID('e159330d-b49e-47da-a930-a09fdd8fa659') metadata=DocumentMetadata(processing_status=None, image_object_paths=None, extra=None) id=UUID('1101a973-12f5-4c49-b195-95666b76d3bd') created=datetime.datetime(2025, 8, 18, 16, 1, 55, 69099, tzinfo=datetime.timezone.utc) edited=datetime.datetime(2025, 8, 18, 16, 1, 55, 69099, tzinfo=datetime.timezone.utc) is_sync_enabled=True extension='pdf' doc_type='DocType.generic' content_hash='9f8e582d32f26f12ca9e5200132174578dbf30ec146f4c195b2dcf52e4e45238' object_path='pdf/7ac1684c5b3a4436a68ffa4c5873114c/raw/ai-hr-2024.pdf'


In [11]:
u = uuid.UUID("9796bc25-fd36-45e5-a96a-17ed94141b51")

In [14]:
f = await client.delete_file(u)
f

IntegrityError: (sqlalchemy.dialects.postgresql.asyncpg.IntegrityError) <class 'asyncpg.exceptions.ForeignKeyViolationError'>: update or delete on table "documents" violates foreign key constraint "fk_document_lines_doc_id_documents" on table "document_lines"
DETAIL:  Key (id)=(9796bc25-fd36-45e5-a96a-17ed94141b51) is still referenced from table "document_lines".
[SQL: DELETE FROM documents WHERE documents.id = $1::UUID]
[parameters: (UUID('9796bc25-fd36-45e5-a96a-17ed94141b51'),)]
(Background on this error at: https://sqlalche.me/e/20/gkpj)

In [12]:
data = await client.es.get_lines_with_vectors(u)
data

[ESLine(line_id='7033b0b4-3606-4d2a-bb7c-bfe988aae43e', doc_id='9796bc25-fd36-45e5-a96a-17ed94141b51', text_content='Внедрение современных систем безопасности,', block_type='SectionHeader', position=105, page_idx=13, sheet_name=None, hierarchy=None, vector=[0.010090422, -0.13585311, 0.0023872855, 0.022814533, 0.019001339, -0.06566449, 0.01623031, 0.089319214, -0.06349937, 0.028647427, 0.0012724111, 0.026256101, -0.020213159, 0.0015794055, -0.022539854, 0.07219216, -0.005663239, 0.029859247, -0.085312136, -0.04753566, -0.01811267, 0.06708636, 0.013612779, 0.085699916, -0.042009763, 0.010082343, -0.046113793, 0.0032113232, -0.00969456, 0.021360349, -0.011746576, -0.046436943, -0.004932108, -0.022895321, 0.00862008, -0.0005342107, 0.007884909, 0.004156543, -0.057294853, -0.011261848, 0.049345315, -0.018888235, 0.05306156, -0.030053137, -0.02006774, 0.0062045185, -0.005630924, -0.008571607, -0.03764721, 0.00969456, -0.010050028, 0.021457294, 0.011593078, -0.027419448, 0.016561542, 0.065535

In [13]:
raw = await client.get_lines_for_document(u)
raw

In [80]:

from typing import List, Optional, Any, Callable

@dataclass
class Settings:
    TEI_URL: str = os.getenv("TEI_URL", "http://localhost:8080")
    TEI_TIMEOUT: float = float(os.getenv("TEI_TIMEOUT", "30"))
    TEI_BATCH_SIZE: int = int(os.getenv("TEI_BATCH_SIZE", "64"))


    RETRY_MAX_ATTEMPTS: int = int(os.getenv("RETRY_MAX_ATTEMPTS", "5"))
    RETRY_BASE_DELAY: float = float(os.getenv("RETRY_BASE_DELAY", "0.5"))
    RETRY_MAX_DELAY: float = float(os.getenv("RETRY_MAX_DELAY", "5.0"))

# =========================
# services/indexer/tei_client.py
# =========================
import logging
from typing import List, Optional, Any

import httpx

settings =  Settings()

async def retry_async(fn: Callable[[], Any], *, name="op"):
    attempt = 0
    while True:
        try:
            return await fn()
        except Exception:
            attempt += 1
            if attempt >= settings.RETRY_MAX_ATTEMPTS:
                raise
            delay = min(settings.RETRY_BASE_DELAY * (2 ** (attempt - 1)), settings.RETRY_MAX_DELAY)
            await asyncio.sleep(delay)
logger = logging.getLogger("indexer.tei")


class TEIClient:
    def __init__(self, base_url: str, timeout: float):
        self.client = httpx.AsyncClient(base_url=base_url, timeout=timeout)

    async def close(self):
        await self.client.aclose()

    @staticmethod
    def _extract_embeddings(data: Any) -> List[List[float]]:
        """
        TEI may return:
          - [{"embedding":[...]}]
          - [[...]]
          - {"data":[{"embedding":[...]}]}  // old shape (we try to support gracefully)
        """
        if isinstance(data, dict) and "data" in data:
            data = data["data"]

        if isinstance(data, list):
            if not data:
                return []
            first = data[0]
            if isinstance(first, dict) and "embedding" in first:
                return [x["embedding"] for x in data]
            if isinstance(first, list):
                return data
        raise ValueError("Unexpected TEI response format")

    async def embed_one(self, text: str) -> Optional[List[float]]:
        if not text or not text.strip():
            return None

        async def _call():
            r = await self.client.post("/embed", json={"inputs": text})
            r.raise_for_status()
            data = r.json()
            vecs = self._extract_embeddings(data)
            return vecs[0] if vecs else None

        vec = await retry_async(_call, name="tei_embed_one")
        logger.debug("TEI embed_one OK", extra={"len": len(vec) if vec else 0})
        return vec

    async def embed_many(self, texts: List[str]) -> List[Optional[List[float]]]:
        if not texts:
            return []
        async def _call():
            r = await self.client.post("/embed", json={"inputs": texts})
            r.raise_for_status()
            data = r.json()
            vecs = self._extract_embeddings(data)
            return vecs[0] if vecs else None
        try:
            vecs = await retry_async(_call, name="tei_embed_batch")
        except Exception:
            return [None for _ in texts]
        # Ensure same length
        if len(vecs) != len(texts):
            # Fallback: pad/truncate
            out = []
            for i in range(len(texts)):
                out.append(vecs[i] if i < len(vecs) else None)
            return out
        return vecs

In [81]:
from __future__ import annotations
import re
import asyncio
from typing import List, Dict, Tuple, Optional
from dataclasses import dataclass, field
from sensory_data_client.models.line import ESLine
import numpy as np
import networkx as nx
from networkx.algorithms import community
import aiohttp # Для мок-клиента


# --- ШАГ 1: Предобработка и пересборка ---

@dataclass
class Paragraph:
    """ Наш новый, более осмысленный юнит анализа """
    id: int
    text_content: str
    source_line_ids: List[str]
    page_indices: List[int]
    # Поля, которые будут заполнены позже
    vector: np.ndarray = field(default_factory=lambda: np.array([]))
    theme_id: Optional[int] = None

def is_noise(text: str, min_len: int = 5) -> bool:
    """ Определяет, является ли строка шумом (артефакты OCR, пунктуация) """
    text = text.strip()
    if len(text) < min_len:
        return True
    # Если строка состоит только из не-буквенно-цифровых символов
    if not any(char.isalnum() for char in text):
        return True
    return False

def is_likely_heading(text: str) -> bool:
    """ Простая эвристика для определения заголовков """
    text = text.strip()
    # Короткая строка, заканчивается без точки, возможно в верхнем регистре
    if len(text) < 80 and not text.endswith('.') and (text.isupper() or text.istitle()):
        return True
    # Нумерованные списки
    if re.match(r"^\d+(\.\d+)*\s", text):
        return True
    return False


# --- ШАГ 2, 3, 4, 5: Основной класс-оркестратор ---

@dataclass
class AnalyzedDocument:
    """ Финальный результат: параграфы, граф и темы """
    paragraphs: List[Paragraph]
    graph: nx.Graph
    themes: Dict[int, List[Paragraph]]

    def get_theme_summary(self, theme_id: int, top_k: int = 3) -> List[str]:
        """ Возвращает самые центральные параграфы темы. Устойчив к темам без векторов. """
        if theme_id not in self.themes:
            raise ValueError(f"Theme {theme_id} not found.")
        theme_paragraphs = self.themes[theme_id]
        if not theme_paragraphs:
            return []
        
        # === ИСПРАВЛЕНИЕ ЗДЕСЬ ===

        # 1. Отбираем параграфы из темы, у которых есть валидный вектор.
        valid_paras = [
            p for p in theme_paragraphs 
            if isinstance(p.vector, np.ndarray) and p.vector.ndim == 1 and p.vector.size > 0
        ]
        
        # 2. ГЛАВНАЯ ПРОВЕРКА: если в этой теме НЕТ параграфов с векторами,
        #    мы не можем их ранжировать. Возвращаем текст первых k параграфов как есть.
        if not valid_paras:
            print(f"ПРЕДУПРЕЖДЕНИЕ: В теме {theme_id} нет параграфов с валидными векторами. Возвращаем сырой текст.")
            return [p.text_content for p in theme_paragraphs[:top_k]]

        # 3. Если мы здесь, значит, векторы есть, и можно безопасно продолжать.
        # Используем np.stack для гарантированного создания 2D-массива.
        theme_vectors = np.stack([p.vector for p in valid_paras])

        centroid = theme_vectors.mean(axis=0)
        centroid /= (np.linalg.norm(centroid) + 1e-9)
        
        # Косинусная близость каждого вектора к центроиду
        similarities = theme_vectors @ centroid.T
        
        # Сортируем по убыванию близости и берем топ-k
        top_indices = np.argsort(similarities)[::-1][:top_k]
        
        # Возвращаем текст соответствующих параграфов
        return [valid_paras[i].text_content for i in top_indices]


    def expand_context(self, paragraph_id: int, hops: int = 1) -> List[Paragraph]:
        """ Находит связанные параграфы, используя граф """
        if not self.graph.has_node(paragraph_id):
            raise ValueError(f"Paragraph {paragraph_id} not found in graph.")
        
        # Находим соседей в графе на расстоянии `hops`
        ego_graph = nx.ego_graph(self.graph, paragraph_id, radius=hops)
        context_ids = sorted(list(ego_graph.nodes()))
        
        return [self.paragraphs[pid] for pid in context_ids]


class DocumentAnalyzer:
    def __init__(self, tei_client: TEIClient, similarity_threshold: float = 0.75):
        self.tei_client = tei_client
        self.similarity_threshold = similarity_threshold

    async def analyze(self, lines: List[ESLine]) -> AnalyzedDocument:
        """ Полный пайплайн анализа документа """
        # 1. Пересобираем строки в параграфы
        print("Шаг 1: Пересборка строк в параграфы...")
        paragraphs = self._reflow_to_paragraphs(lines)
        if not paragraphs:
            return AnalyzedDocument([], nx.Graph(), {})

        # 2. Векторизуем параграфы
        print("Шаг 2: Векторизация параграфов...")
        paragraphs = await self._embed_paragraphs(paragraphs)

        # 3. Строим граф документа
        print("Шаг 3: Построение графа документа...")
        graph = self._build_document_graph(paragraphs)
        
        # 4. Находим тематические сообщества
        print("Шаг 4: Поиск тематических сообществ...")
        themes = self._find_themes(graph, paragraphs)
        
        print("Анализ завершен.")
        return AnalyzedDocument(paragraphs, graph, themes)

    def _reflow_to_paragraphs(self, lines: List[ESLine]) -> List[Paragraph]:
        # Сортируем строки, как они идут в документе
        lines.sort(key=lambda ln: (ln.page_idx, ln.position))
        
        paragraphs_text = []
        current_paragraph = []
        current_line_ids = []
        current_pages = set()

        def flush_paragraph():
            if current_paragraph:
                text = " ".join(current_paragraph).strip()
                if not is_noise(text, min_len=20): # Фильтруем слишком короткие параграфы
                    paragraphs_text.append(
                        (text, list(current_line_ids), sorted(list(current_pages)))
                    )
                current_paragraph.clear()
                current_line_ids.clear()
                current_pages.clear()

        for line in lines:
            text = line.text_content.strip()
            if not text or is_noise(text):
                continue

            # Правило для начала нового параграфа:
            # 1. Это явный заголовок.
            # 2. Предыдущая строка закончилась на знак препинания, а эта начинается с заглавной.
            # 3. Предыдущий параграф уже есть.
            new_paragraph_condition = False
            if is_likely_heading(text):
                new_paragraph_condition = True
            elif current_paragraph and current_paragraph[-1].endswith(('.', '!', '?')):
                new_paragraph_condition = True

            if new_paragraph_condition:
                flush_paragraph()

            current_paragraph.append(text.rstrip('-')) # Удаляем дефисы-переносы
            current_line_ids.append(line.line_id)
            current_pages.add(line.page_idx)
        
        flush_paragraph() # Сохраняем последний параграф

        return [
            Paragraph(id=i, text_content=text, source_line_ids=ids, page_indices=pages)
            for i, (text, ids, pages) in enumerate(paragraphs_text)
        ]

    async def _embed_paragraphs(self, paragraphs: List[Paragraph]) -> List[Paragraph]:
        texts = [p.text_content for p in paragraphs]
        vectors = await self.tei_client.embed_many(texts)
        for p, vec in zip(paragraphs, vectors):
            p.vector = np.array(vec, dtype=np.float32)
        return paragraphs

    def _build_document_graph(self, paragraphs: List[Paragraph]) -> nx.Graph:
        G = nx.Graph()
        for i, p in enumerate(paragraphs):
            G.add_node(i, text=p.text_content[:100] + "...")
            if i > 0: G.add_edge(i - 1, i, weight=0.5, type='structural')
        
        # === ФИНАЛЬНОЕ ИСПРАВЛЕНИЕ ЗДЕСЬ ===

        # 1. Собрать все валидные векторы и их оригинальные индексы.
        #    Валидный вектор - это 1D ndarray.
        valid_vectors_map = {
            i: p.vector for i, p in enumerate(paragraphs)
            if isinstance(p.vector, np.ndarray) and p.vector.ndim == 1
        }
        
        if len(valid_vectors_map) < 2: return G

        # 2. Определить каноническую размерность и отфильтровать несоответствия.
        canonical_dim = next(iter(valid_vectors_map.values())).shape[0]
        
        final_indices = []
        final_vectors_list = []
        for idx, vec in valid_vectors_map.items():
            if vec.shape[0] == canonical_dim:
                final_indices.append(idx)
                final_vectors_list.append(vec)
        
        if len(final_indices) < 2: return G

        # 3. ГАРАНТИРОВАННОЕ СОЗДАНИЕ 2D-МАТРИЦЫ
        #    Мы создаем пустую матрицу нужного размера и заполняем ее.
        #    Этот метод абсолютно нечувствителен к проблемам с dtype=object.
        num_valid = len(final_indices)
        vectors_matrix = np.zeros((num_valid, canonical_dim), dtype=np.float32)
        for i, vec in enumerate(final_vectors_list):
            vectors_matrix[i] = vec
            
        # 4. Добавим assertion, чтобы быть на 100% уверенными.
        #    Если здесь будет ошибка, значит проблема в логике выше, а не в NumPy.
        assert vectors_matrix.ndim == 2, f"Критическая ошибка: матрица векторов осталась 1D с формой {vectors_matrix.shape}"

        # 5. Теперь все вычисления абсолютно безопасны.
        norms = np.linalg.norm(vectors_matrix, axis=1, keepdims=True)
        vectors_norm = vectors_matrix / (norms + 1e-9) # Добавляем эпсилон для стабильности
        
        similarity_matrix = vectors_norm @ vectors_norm.T
        
        # 6. Находим близкие пары и добавляем ребра, используя финальные ОРИГИНАЛЬНЫЕ индексы.
        similar_pairs = np.argwhere(similarity_matrix > self.similarity_threshold)
        
        for local_i, local_j in similar_pairs:
            if local_i < local_j:
                original_i = final_indices[local_i]
                original_j = final_indices[local_j]
                
                G.add_edge(original_i, original_j, 
                           weight=float(similarity_matrix[local_i, local_j]), 
                           type='semantic')
        
        return G

    def _find_themes(self, graph: nx.Graph, paragraphs: List[Paragraph]) -> Dict[int, List[Paragraph]]:
        # Используем алгоритм Лувена для поиска сообществ
        # Он хорошо работает на взвешенных графах
        communities = community.louvain_communities(graph, weight='weight', seed=42)
        
        themes = {}
        for theme_id, paragraph_indices in enumerate(communities):
            theme_paragraphs = []
            for p_id in sorted(list(paragraph_indices)):
                para = paragraphs[p_id]
                para.theme_id = theme_id
                theme_paragraphs.append(para)
            themes[theme_id] = theme_paragraphs
        return themes


In [82]:

tei_client = TEIClient('http://10.10.0.70:8080', 900)

vec = await tei_client.embed_one("Привет")

In [83]:
analyzer = DocumentAnalyzer(tei_client, similarity_threshold=0.9)
analyzed_doc = await analyzer.analyze(data)

Шаг 1: Пересборка строк в параграфы...
Шаг 2: Векторизация параграфов...
Шаг 3: Построение графа документа...
Шаг 4: Поиск тематических сообществ...
Анализ завершен.


In [86]:
for theme_id in analyzed_doc.themes.keys():
    print(theme_id)
    summary = analyzed_doc.get_theme_summary(theme_id, top_k=4)

0
ПРЕДУПРЕЖДЕНИЕ: В теме 0 нет параграфов с валидными векторами. Возвращаем сырой текст.
1
ПРЕДУПРЕЖДЕНИЕ: В теме 1 нет параграфов с валидными векторами. Возвращаем сырой текст.
2
ПРЕДУПРЕЖДЕНИЕ: В теме 2 нет параграфов с валидными векторами. Возвращаем сырой текст.
3
ПРЕДУПРЕЖДЕНИЕ: В теме 3 нет параграфов с валидными векторами. Возвращаем сырой текст.
4
ПРЕДУПРЕЖДЕНИЕ: В теме 4 нет параграфов с валидными векторами. Возвращаем сырой текст.
5
ПРЕДУПРЕЖДЕНИЕ: В теме 5 нет параграфов с валидными векторами. Возвращаем сырой текст.
6
ПРЕДУПРЕЖДЕНИЕ: В теме 6 нет параграфов с валидными векторами. Возвращаем сырой текст.
7
ПРЕДУПРЕЖДЕНИЕ: В теме 7 нет параграфов с валидными векторами. Возвращаем сырой текст.
8
ПРЕДУПРЕЖДЕНИЕ: В теме 8 нет параграфов с валидными векторами. Возвращаем сырой текст.
9
ПРЕДУПРЕЖДЕНИЕ: В теме 9 нет параграфов с валидными векторами. Возвращаем сырой текст.
10
ПРЕДУПРЕЖДЕНИЕ: В теме 10 нет параграфов с валидными векторами. Возвращаем сырой текст.


In [87]:
analyzed_doc.themes

{0: [Paragraph(id=0, text_content='Примеры  кейсов Исследование медиаконтента  сервисов «Газпромбанк»', source_line_ids=['8feb96dd-3c3c-4531-8547-f64baa247dc0', 'dcd39fd5-743b-43b0-9ecb-2d73aa38bd1c'], page_indices=[0], vector=array(nan, dtype=float32), theme_id=0),
  Paragraph(id=1, text_content='Газпромбанк Общие сведения 1.1. Опыт команды', source_line_ids=['c3158c7e-7ab7-4d1f-bef4-362509074211', '196746fc-c542-4b12-a29d-af3fb6f91a49', '46ff7e00-3fa5-4755-bd95-f2c5ee93e2b7'], page_indices=[1, 2], vector=array(nan, dtype=float32), theme_id=0),
  Paragraph(id=2, text_content="Описание Наименование: ООО «СенсориЛаб». Дата основания: 2018 год. SensoryLAB — R'n'D лаборатория нейромаркетинговых, сенсорных и Data Science технологий для разработки и тестирования бизнес-гипотез.", source_line_ids=['11b67ad3-aaf2-4492-adca-bbc71512b842', '8d3eaaae-fc7a-41f8-ae32-1303dc4f5c94'], page_indices=[2], vector=array(nan, dtype=float32), theme_id=0),
  Paragraph(id=3, text_content='Направления работ О

In [53]:
import asyncio
import typer
import logging
import sys
if sys.platform == "win32":
    # Принудительно устанавливаем политику, которая использует SelectorEventLoop.
    # Это решает проблему с ProactorEventLoop по умолчанию в Windows.
    asyncio.set_event_loop_policy(asyncio.WindowsSelectorEventLoopPolicy())
    
from sensory_data_client import DataClient, get_settings, DataClientConfig, PostgresConfig, MinioConfig, create_data_client
from sensory_data_client.models.document import DocumentCreate, DocumentMetadata

from sensory_data_client.config import get_settings
from sensory_data_client import create_data_client
from sensory_data_client.exceptions import DataClientError
from sensory_data_client.utils.cli_utils import get_rich_console
settings = get_settings()
# ИМПОРТИРУЕМ Base из ORM и create_async_engine
from sensory_data_client.db.base import Base
from sqlalchemy.ext.asyncio import create_async_engine


app = typer.Typer(help="CLI for sensory-data-client management.")
logger = logging.getLogger(__name__)
console = get_rich_console()
cfg = DataClientConfig(postgres = PostgresConfig(user = "postgres",
                                                           password = "postgres",
                                                           host = "10.10.0.70",
                                                           port=5422), 
                                            minio = MinioConfig(endpoint="10.10.0.70:9008",  bucket = "documents"))

engine = create_async_engine(cfg.postgres.get_pg_dsn())
async with engine.begin() as conn:
    await conn.run_sync(Base.metadata.create_all)
await engine.dispose()


In [55]:

# Шаг 4: Вызываем асинхронный метод с `await`
try:
    # Ваш метод `upload_file` скорее всего захочет получить чистое имя файла,
    # а не весь путь. file_path.name идеально для этого подходит.
    result_document = await client.upload_file(
        file_name=file_path.name,
        content=file_content,
        meta=document_meta
    )
    
    print("\n✅ Успешно загружен документ!")
    print(f"   ID в базе: {result_document.id}")
    print(f"   Путь в хранилище: {result_document}")

except Exception as e:
    print(f"❌ Произошла ошибка во время загрузки: {e}")


❌ Произошла ошибка во время загрузки: Failed to save document metadata: (sqlalchemy.dialects.postgresql.asyncpg.IntegrityError) <class 'asyncpg.exceptions.UniqueViolationError'>: duplicate key value violates unique constraint "uq_documents_owner_userdoc"
DETAIL:  Key (owner_id, user_document_id)=(0c8608a8-6488-442e-be2c-1a431a0a3c04, 8da97dc0-0dc1-4155-afca-a613483fa676) already exists.
[SQL: INSERT INTO documents (id, user_document_id, stored_file_id, name, owner_id, access_group_id, metadata) VALUES ($1::UUID, $2::VARCHAR, $3::INTEGER, $4::VARCHAR, $5::UUID, $6::UUID, $7::JSONB) RETURNING documents.created, documents.edited]
[parameters: (UUID('ff949cd2-9d15-416b-980f-d68c39aa722e'), '8da97dc0-0dc1-4155-afca-a613483fa676', 1, 'ai-hr-2024.pdf', UUID('0c8608a8-6488-442e-be2c-1a431a0a3c04'), UUID('8f088d88-fd3b-4c86-af38-2196b6cab3cc'), '{"processing_status": null, "image_object_paths": null, "extra": null}')]
(Background on this error at: https://sqlalche.me/e/20/gkpj)


In [52]:
doc_meta = await client.metarepo.get("8a95427a-18d7-4d50-8ec6-1b631ae70de6")

ValidationError: 2 validation errors for DocumentInDB
owner_id
  Input should be a valid string [type=string_type, input_value=UUID('8f16fc0c-e4d0-42ef-89a2-3aa787801f56'), input_type=UUID]
    For further information visit https://errors.pydantic.dev/2.10/v/string_type
access_group_id
  Input should be a valid string [type=string_type, input_value=UUID('8f088d88-fd3b-4c86-af38-2196b6cab3cc'), input_type=UUID]
    For further information visit https://errors.pydantic.dev/2.10/v/string_type

In [ ]:
cfg = DataClientConfig(postgres = PostgresConfig(user = "postgres",
                                                           password = "postgres",
                                                           host = "10.10.0.70",
                                                           port=5422), 
                                            minio = MinioConfig(endpoint="10.10.0.70:9008",  bucket = "documents"))
